In [27]:
%matplotlib qt
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.pylab as pylb
from matplotlib.animation import FFMpegWriter

params = {'figure.figsize': (25, 15), 'legend.fontsize': 15, 'axes.labelsize': 15, 'axes.titlesize': 15, 
          'xtick.labelsize': 15, 'ytick.labelsize': 15}
pylb.rcParams.update(params)

In [28]:
#define first simulation function
def kepler(v, p):
    px = p[0]
    py = p[1]
    vx = v[0]
    vy = v[1]
    
    d = np.sqrt(px**2+py**2)
    ax = -g*ms*px/d**3
    ay = -g*ms*py/d**3
    vx += ax*dt
    vy += ay*dt
    px += vx*dt
    py += vy*dt
    
    v = [vx, vy]
    p = [px, py]
    return v, p

In [29]:
#define second simulation function
def kepler2(v, p):
    px = p[0]
    py = p[1]
    vx = v[0]
    vy = v[1]
    
    dsr = np.sqrt((px-ps[0])**2+(py-ps[1])**2)
    axs = -g*ms*(px-ps[0])/dsr**3
    ays = -g*ms*(py-ps[1])/dsr**3
    
    der = np.sqrt((px-pe[0])**2+(py-pe[1])**2)
    axe = -g*me*(px-pe[0])/der**3
    aye = -g*me*(py-pe[1])/der**3
    
    dmr = np.sqrt((px-pm[0])**2+(py-pm[1])**2)
    axm = -g*mm*(px-pm[0])/dmr**3
    aym = -g*mm*(py-pm[1])/dmr**3
    
    #print('dsr=', dsr,'der=', der,'dmr=', dmr,)
    #print('axs=', axs, 'ays=', ays)
    #print('axe=', axe, 'aye=', aye)
    #print('axm=', axm, 'aym=', aym)
    #print()
    
    ax = axs+axe#+axm
    ay = ays+aye#+aym
    vx += ax*dt
    vy += ay*dt
    px += vx*dt
    py += vy*dt
    
    v = [vx, vy]
    p = [px, py]
    return v, p

In [30]:
#define variables
ms = 1.989e30
me = 5.972e24
mm = 6.417e23
mr = 100

de = 1.496e11
dm = 2.280e11

rs = 695508
re = 6371
rm = 3389

g = 6.674e-11

ue = (ms*me)/(ms+me)
we = np.sqrt((g*ms*me)/(ue*de**3))
Pe = np.sqrt((4*np.pi**2*de**3)/(g*(ms+me)))

um = (ms*mm)/(ms+mm)
wm = np.sqrt((g*ms*mm)/(um*dm**3))
Pm = np.sqrt((4*np.pi**2*dm**3)/(g*(ms+mm)))

In [99]:
#picture of simulation
ps = [0, 0]
pe = [de, 0]
pm = [dm, 0]

ve = [we*pe[1], we*pe[0]]
vm = [wm*pm[1], wm*pm[0]]

xss = [ps[0]]
yss = [ps[1]]
xse = [pe[0]]
yse = [pe[1]]
xsm = [pm[0]]
ysm = [pm[1]]

stages = ['waiting', 'waiting', 'waiting', 'waiting', 'waiting', 'waiting', 'waiting', 'waiting', 'waiting']
degrees1 = [10, 20, 30, 40, 50, 60, 70, 80, 90]
degrees2 = [50, 60, 70, 80, 90, 100, 110, 120, 130]
degrees3 = [-90, -80, -70, -60, -50, -40, -30, -20, -10]
degrees4 = [-130, -120, -110, -100, -90, -80, -70, -60, -50]
angles = np.radians(degrees3)
vrs = [[], [], [], [], [], [], [], [], []]
prs = [[], [], [], [], [], [], [], [], []]
xsrs = [[], [], [], [], [], [], [], [], []]
ysrs = [[], [], [], [], [], [], [], [], []]

t = 0
event = 2*Pe/4
dt = Pe/500

while t < 4*Pe:
    ve, pe = kepler(ve, pe)
    vm, pm = kepler(vm, pm)
    xss.append(ps[0])
    yss.append(ps[1])
    xse.append(pe[0])
    yse.append(pe[1])
    xsm.append(pm[0])
    ysm.append(pm[1])

    if t > event:
        for i in range(len(stages)):
            if stages[i] == 'waiting':
                vrx = (vm[0]*np.cos(angles[i])-vm[1]*np.sin(angles[i]))/1.5
                vry = (vm[0]*np.sin(angles[i])+vm[1]*np.cos(angles[i]))/1.5
                vrs[i] = [vrx, vry]
                prs[i] = [pm[0]-1000, pm[1]-1000]
                xsrs[i].append(prs[i][0])
                ysrs[i].append(prs[i][1])
                stages[i] = 'flying'

    for i in range(len(stages)):
        if stages[i] == 'flying':
            vrs[i], prs[i] = kepler2(vrs[i], prs[i])
            xsrs[i].append(prs[i][0])
            ysrs[i].append(prs[i][1])

            dsr = np.sqrt((prs[i][0]-ps[0])**2+(prs[i][1]-ps[1])**2)
            der = np.sqrt((prs[i][0]-pe[0])**2+(prs[i][1]-pe[1])**2)
            dmr = np.sqrt((prs[i][0]-pm[0])**2+(prs[i][1]-pm[1])**2)
            val = 1e10
            if dsr < val:
                stages[i] = 'hit'
                print('Rock #', i+1, 'hit the Sun')
            if der < val:
                stages[i] = 'hit'
                print('Rock #', i+1, 'hit Earth')
            if dmr < val and t > event+(event/10):
                stages[i] = 'hit'
                print('Rock #', i+1, 'hit Mars')

    t += dt

plt.figure(figsize=(15, 15))
plt.plot(ps[0], ps[1], 'yo', label='Sun')
plt.plot(pe[0], pe[1], 'bo', label='Earth')
plt.plot(pm[0], pm[1], 'ro', label='Mars')
plt.plot(xss, yss, 'y')
plt.plot(xse, yse, 'b')
plt.plot(xsm, ysm, 'r')
plt.plot(prs[0][0], prs[0][1], 'k.', label='Ejected Rocks')
for i in range(len(stages)):
    plt.plot(prs[i][0], prs[i][1], 'k.')
    plt.plot(xsrs[i], ysrs[i], 'k')
plt.xlim(-3e11, 3e11)
plt.ylim(-3e11, 3e11)
plt.legend(loc=2)
plt.xlabel('Distance (Meters)')
plt.ylabel('Distance (Meters)')
plt.show()

Rock # 3 hit the Sun
Rock # 2 hit the Sun
Rock # 1 hit the Sun
Rock # 9 hit Earth


In [98]:
#video of simulation
fig = plt.figure(figsize=(10, 10))
metadata = dict(title='Final Project', artist='Matplotlib',comment='Orbits.')
writer = FFMpegWriter(fps=15, metadata=metadata)

with writer.saving(fig, "final.mp4", dpi=200):

    ps = [0, 0]
    pe = [de, 0]
    pm = [dm, 0]

    ve = [we*pe[1], we*pe[0]]
    vm = [wm*pm[1], wm*pm[0]]

    xss = [ps[0]]
    yss = [ps[1]]
    xse = [pe[0]]
    yse = [pe[1]]
    xsm = [pm[0]]
    ysm = [pm[1]]

    stages = ['waiting', 'waiting', 'waiting', 'waiting', 'waiting', 'waiting', 'waiting', 'waiting', 'waiting']
    degrees1 = [10, 20, 30, 40, 50, 60, 70, 80, 90]
    degrees2 = [50, 60, 70, 80, 90, 100, 110, 120, 130]
    degrees3 = [-90, -80, -70, -60, -50, -40, -30, -20, -10]
    degrees4 = [-130, -120, -110, -100, -90, -80, -70, -60, -50]
    angles = np.radians(degrees3)
    vrs = [[], [], [], [], [], [], [], [], []]
    prs = [[], [], [], [], [], [], [], [], []]
    xsrs = [[], [], [], [], [], [], [], [], []]
    ysrs = [[], [], [], [], [], [], [], [], []]

    t = 0
    event = 2*Pe/4
    dt = Pe/500

    while t < 4*Pe:
        ve, pe = kepler(ve, pe)
        vm, pm = kepler(vm, pm)
        xss.append(ps[0])
        yss.append(ps[1])
        xse.append(pe[0])
        yse.append(pe[1])
        xsm.append(pm[0])
        ysm.append(pm[1])

        if t > event:
            for i in range(len(stages)):
                if stages[i] == 'waiting':
                    vrx = (vm[0]*np.cos(angles[i])-vm[1]*np.sin(angles[i]))/1.5
                    vry = (vm[0]*np.sin(angles[i])+vm[1]*np.cos(angles[i]))/1.5
                    vrs[i] = [vrx, vry]
                    prs[i] = [pm[0]-1000, pm[1]-1000]
                    xsrs[i].append(prs[i][0])
                    ysrs[i].append(prs[i][1])
                    stages[i] = 'flying'

        for i in range(len(stages)):
            if stages[i] == 'flying':
                vrs[i], prs[i] = kepler2(vrs[i], prs[i])
                xsrs[i].append(prs[i][0])
                ysrs[i].append(prs[i][1])

                dsr = np.sqrt((prs[i][0]-ps[0])**2+(prs[i][1]-ps[1])**2)
                der = np.sqrt((prs[i][0]-pe[0])**2+(prs[i][1]-pe[1])**2)
                dmr = np.sqrt((prs[i][0]-pm[0])**2+(prs[i][1]-pm[1])**2)
                val = 1e10
                if dsr < val:
                    stages[i] = 'hit'
                    print('Rock #', i+1, 'hit the Sun')
                if der < val:
                    stages[i] = 'hit'
                    print('Rock #', i+1, 'hit Earth')
                if dmr < val and t > event+(event/10):
                    stages[i] = 'hit'
                    print('Rock #', i+1, 'hit Mars')

        t += dt

        plt.clf()
        
        plt.plot(ps[0], ps[1], 'yo', label='Sun')
        plt.plot(pe[0], pe[1], 'bo', label='Earth')
        plt.plot(pm[0], pm[1], 'ro', label='Mars')
        plt.plot(xss, yss, 'y')
        plt.plot(xse, yse, 'b')
        plt.plot(xsm, ysm, 'r')
        if prs[0] != []:
            plt.plot(prs[0][0], prs[0][1], 'k.', label='Ejected Rocks')
            for i in range(len(stages)):
                plt.plot(prs[i][0], prs[i][1], 'k.')
                plt.plot(xsrs[i], ysrs[i], 'k')
        plt.xlim(-3e11, 3e11)
        plt.ylim(-3e11, 3e11)
        plt.legend(loc=2)
        plt.xlabel('Distance (Meters)')
        plt.ylabel('Distance (Meters)')
        plt.show()
        
        plt.draw()
        writer.grab_frame()

Rock # 3 hit the Sun
Rock # 2 hit the Sun
Rock # 1 hit the Sun
Rock # 9 hit Earth
